### LAX Prior Elicitation 4 Block Tower Results Visualizer
Author : Catherine Wong, adapted by Will McCarthy

This notebook visualizes results from the LAX prior elicitation.

Preview on GitHub:
https://htmlpreview.github.io/?https://raw.githubusercontent.com/cogtoolslab/lax/master/analysis/lax-prior-elicitation-drawing-results-visualizer.html?token=ABK3B5AV4P3VTAK3Q3QCTKLA7BUOC

In [7]:
import os, csv, sys
import pandas as pd
from functools import reduce


#### Join the dataframes on the stimuli ID

In [26]:
import pandas as pd
from IPython.display import Image, HTML

def add_numbers_and_space(responses):
    responses = [f"{id}: {response}" for (id, response) in enumerate(responses)]
    responses = '\n'.join(responses)
    return responses

def group_by_stim_url(df, config_name):
    df[config_name] = df[['stimURL','responses']].groupby(['stimURL'])['responses'].transform(lambda responses: add_numbers_and_space(responses))
    df[['stimURL', config_name]].drop_duplicates()
    return df[['stimURL', config_name]]

def group_by_stim_id(df, config_name):
    df[config_name] = df[['stimId','responses']].groupby(['stimId'])['responses'].transform(lambda responses: add_numbers_and_space(responses))
    df[['stimId', config_name]].drop_duplicates()
    return df[['stimId', config_name]]

def path_to_image_html(path):
    '''
     This function essentially convert the image url to 
     '<img src="'+ path + '"/>' format. And one can put any
     formatting adjustments to control the height, aspect ratio, size etc.
     within as in the below example. 
    '''

    return '<img src="'+ path + '" style=max-width:200px"/>'


def stimId_to_s3URL(domain, subdomain, stimID):
    
    if domain == 'structures':
        url =  "https://lax-{}-{}-all.s3.amazonaws.com/".format(domain, 
                                                                subdomain)\
               + "lax-{}-{}-{}-all.png".format(domain,
                                      subdomain,
                                      str(stimID).zfill(3))
    else: #check this
        url =  "https://lax-{}-{}-all.s3.amazonaws.com/".format(domain, 
                                                                subdomain)\
               + "lax-{}-{}-all-{}.png".format(domain,
                                      subdomain,
                                      str(stimID).zfill(3))

    return url
    

def stimId_to_html(stimId, domain = 'structures', subdomain = 'bridge'):
    '''
     This function essentially convert the image url to 
     '<img src="'+ path + '"/>' format. And one can put any
     formatting adjustments to control the height, aspect ratio, size etc.
     within as in the below example. 
    '''
    stimURL = stimId_to_s3URL(domain, subdomain, stimId) 
    return '<img src="'+ stimURL + '" style=max-width:200px"/>'




#### Load the raw results CSVs

In [27]:
WORKER_ID, TRIAL_TYPE, TRIAL_INDEX, CONDITION, STIM_URL, RESPONSES = \
"workerID", "trial_type", "trial_index", "condition", "stimURL", "responses"


In [28]:
results_csv_directory = "../../results/csv"

results_to_visualize = ['lax_corpus_1k_trial.csv']

result_csv_to_dataframe = {}
for result_csv in results_to_visualize:
    result_csv_to_dataframe[result_csv] = pd.read_csv(os.path.join(results_csv_directory, result_csv))
    result_csv_to_dataframe[result_csv]['config_name'] = result_csv

In [29]:
result_csv = 'lax_corpus_1k_trial.csv'
df_trial = pd.read_csv(os.path.join(results_csv_directory, result_csv))

In [30]:
subdomains = {
    'structures' :  ['bridge', 'castle', 'house', 'city'],
    'drawing' :  ['nuts-bolts','wheels','furniture','dials']
}

domains = list(subdomains.keys())

### Visualize all responses

In [32]:
for domain in domains:
    for subdomain in subdomains[domain]:
        
        df_subdomain = df_trial[(df_trial.complete_dataset) &
                                (df_trial.stimId != 'demo_stim') &
                                (df_trial.subdomain == subdomain)].reset_index()
        
        
        grouped_df_list = [group_by_stim_id(df, config_name) for (config_name, df) in {subdomain: df_subdomain}.items()]
        reduced_df = reduce(lambda x, y: pd.merge(x, y, on = ['stimId','domain','subdomain']), grouped_df_list).drop_duplicates()

        display(HTML(reduced_df.to_html(escape=False,
                                formatters=dict(stimId=
                                                lambda x:(stimId_to_html(x, domain = domain, subdomain = subdomain))))
                        .replace("\\n","<br>=======<br><br>").replace("'what-","<br>'what-")))



### Visualize towers with smallest/largest word counts

In [24]:
# add mean word count for each stim
what_word_sum_means = df_trial.groupby(['domain','subdomain','stimId']).mean()['what_word_sum'].reset_index()
what_word_sum_means = what_word_sum_means.rename(columns={'what_word_sum':'what_word_mean'})
what_word_sum_means
df_trial = df_trial.merge(what_word_sum_means, how='left', on=['domain','subdomain','stimId'])

In [25]:
from skimage import io
import matplotlib.pyplot as plt

#### Most words

In [148]:
# display items for each domain with highest mean word count
top_n = 10

for domain in domains:
    for subdomain in subdomains[domain]:
        
        df_subdomain = df_trial[(df_trial.complete_dataset) &
                                 (df_trial.stimId != 'demo_stim') &
                                 (df_trial.subdomain == subdomain)]\
                                    .sort_values(['what_word_mean','stimId'], ascending=False)
                
        
        grouped_df_list = [group_by_stim_id(df, config_name) for (config_name, df) in {subdomain: df_subdomain}.items()]
        reduced_df = reduce(lambda x, y: pd.merge(x, y, on = ['stimId','domain','subdomain']), grouped_df_list).drop_duplicates()

        display(HTML(reduced_df.head(top_n)\
                        .to_html(escape=False,
                                formatters=dict(stimId=
                                                lambda x:(stimId_to_html(x, domain = domain, subdomain = subdomain))))
                        .replace("\\n","<br>=======<br><br>")))
        
        
        

#### Least words

In [149]:
# display items for each domain with lowest mean word count

bottom_n = 10

for domain in domains:
    for subdomain in subdomains[domain]:
        
        df_subdomain = df_trial[(df_trial.complete_dataset) &
                                 (df_trial.stimId != 'demo_stim') &
                                 (df_trial.subdomain == subdomain)]\
                                    .sort_values(['what_word_mean','stimId'], ascending=False)
                
        
        grouped_df_list = [group_by_stim_id(df, config_name) for (config_name, df) in {subdomain: df_subdomain}.items()]
        reduced_df = reduce(lambda x, y: pd.merge(x, y, on = ['stimId','domain','subdomain']), grouped_df_list).drop_duplicates()

        display(HTML(reduced_df.tail(top_n)\
                        .to_html(escape=False,
                                formatters=dict(stimId=
                                                lambda x:(stimId_to_html(x, domain = domain, subdomain = subdomain))))
                        .replace("\\n","<br>=======<br><br>")))
        
        
        

In [126]:
domain = 'structures'
subdomain = 'house'

df_subdomain = df_trial[(df_trial.complete_dataset) &
         (df_trial.stimId != 'demo_stim') &
         (df_trial.subdomain == subdomain)].sort_values(['what_word_mean','stimId'], ascending=False)

# top_structures = df_subdomain.groupby(['domain','subdomain','stimId'])['what_word_mean'].first().reset_index() # get mean is precomputed above

grouped_df_list = [group_by_stim_id(df, config_name) for (config_name, df) in {subdomain: df_subdomain}.items()]
reduced_df = reduce(lambda x, y: pd.merge(x, y, on = ['stimId','domain','subdomain']), grouped_df_list).drop_duplicates()

HTML(reduced_df.to_html(escape=False,
                        formatters=dict(stimId=
                                        lambda x:(stimId_to_html(x, domain = domain, subdomain = subdomain))))
                .replace("\\n","<br>=======<br><br>"))


### What did human subjects respond for the raw stimuli in each image and condition?

In [55]:
# start from scratch



grouped_df_list = [group_by_stim_id(df, config_name) for (config_name, df) in {subdomain: df_subdomain}.items()]
reduced_df = reduce(lambda x, y: pd.merge(x, y, on = ['stimId','domain','subdomain']), grouped_df_list).drop_duplicates()

HTML(reduced_df.to_html(escape=False,
                        formatters=dict(stimId=
                                        lambda x:(stimId_to_html(x, domain = domain, subdomain = subdomain))))
                .replace("\\n","<br>=======<br><br>"))



In [51]:
# grouped_df_list = [group_by_stim_id(df, config_name) for (config_name, df) in result_csv_to_dataframe.items()]
# reduced_df = reduce(lambda x, y: pd.merge(x, y, on = ['stimId','domain','subdomain']), grouped_df_list).drop_duplicates()

# HTML(reduced_df.to_html(escape=False,
#                         formatters=dict(stimId=
#                                         lambda x:(stimId_to_html(x, domain = domain, subdomain = subdomain))))
#                 .replace("\\n","<br>=======<br><br>"))


In [6]:
from functools import reduce

grouped_df_list = [group_by_stim_id(df, config_name) for (config_name, df) in result_csv_to_dataframe.items()]
reduced_df = reduce(lambda x, y: pd.merge(x, y, on = 'stimId'), grouped_df_list).drop_duplicates()

HTML(reduced_df.to_html(escape=False,
                        formatters=dict(stimId=
                                        lambda x:(stimId_to_tower_html(x, subdomain = subdomain))))
                .replace("\\n","<br>=======<br><br>"))


In [76]:
from functools import reduce

grouped_df_list = [group_by_stim_id(df, config_name) for (config_name, df) in result_csv_to_dataframe.items()]
reduced_df = reduce(lambda x, y: pd.merge(x, y, on = 'stimId'), grouped_df_list).drop_duplicates()

HTML(reduced_df.to_html(escape=False,
                        formatters=dict(stimId=
                                        lambda x:(stimId_to_tower_html(x, subdomain = subdomain))))
                .replace("\\n","<br>=======<br><br>"))
